In [0]:
# read data from csv file
olympics_data = spark.read.format("csv") \
                          .option("header", "true") \
                          .option("inferSchema", "true") \
                          .load("/FileStore/datasets/summer.csv")

olympics_data.display()

Year City Sport Discipline Athlete Country Gender Event Medal 1896 Athens Aquatics Swimming HAJOS, Alfred HUN Men 100M Freestyle Gold 1896 Athens Aquatics Swimming HERSCHMANN, Otto AUT Men 100M Freestyle Silver 1896 Athens Aquatics Swimming DRIVAS, Dimitrios GRE Men 100M Freestyle For Sailors Bronze 1896 Athens Aquatics Swimming MALOKINIS, Ioannis GRE Men 100M Freestyle For Sailors Gold 1896 Athens Aquatics Swimming CHASAPIS, Spiridon GRE Men 100M Freestyle For Sailors Silver 1896 Athens Aquatics Swimming CHOROPHAS, Efstathios GRE Men 1200M Freestyle Bronze 1896 Athens Aquatics Swimming HAJOS, Alfred HUN Men 1200M Freestyle Gold 1896 Athens Aquatics Swimming ANDREOU, Joannis GRE Men 1200M Freestyle Silver 1896 Athens Aquatics Swimming CHOROPHAS, Efstathios GRE Men 400M Freestyle Bronze 1896 Athens Aquatics Swimming NEUMANN, Paul AUT Men 400M Freestyle Gold 1896 Athens Aquatics Swimming PEPANOS, Antonios GRE Men 400M Freestyle Silver 1896 Athens Athletics Athletics LANE, Francis USA Men 100M Bronze 1896 Athens Athletics Athletics SZOKOLYI, Alajos HUN Men 100M Bronze 1896 Athens Athletics Athletics BURKE, Thomas USA Men 100M Gold 1896 Athens Athletics Athletics HOFMANN, Fritz GER Men 100M Silver 1896 Athens Athletics Athletics CURTIS, Thomas USA Men 110M Hurdles Gold 1896 Athens Athletics Athletics GOULDING, Grantley GBR Men 110M Hurdles Silver 1896 Athens Athletics Athletics LERMUSIAUX, Albin FRA Men 1500M Bronze 1896 Athens Athletics Athletics FLACK, Edwin AUS Men 1500M Gold 1896 Athens Athletics Athletics BLAKE, Arthur USA Men 1500M Silver 1896 Athens Athletics Athletics GMELIN, Charles GBR Men 400M Bronze 1896 Athens Athletics Athletics BURKE, Thomas USA Men 400M Gold 1896 Athens Athletics Athletics JAMISON, Herbert USA Men 400M Silver 1896 Athens Athletics Athletics GOLEMIS, Dimitrios GRE Men 800M Bronze 1896 Athens Athletics Athletics FLACK, Edwin AUS Men 800M Gold 1896 Athens Athletics Athletics DANI, Nandor HUN Men 800M Silver 1896 Athens Athletics Athletics VERSIS, Sotirios GRE Men Discus Throw Bronze 1896 Athens Athletics Athletics GARRETT, Robert USA Men Discus Throw Gold 1896 Athens Athletics Athletics PARASKEVOPOULOS, Panagiotis GRE Men Discus Throw Silver 1896 Athens Athletics Athletics CLARK, Ellery USA Men High Jump Gold 1896 Athens Athletics Athletics CONNOLLY, James USA Men High Jump Silver 1896 Athens Athletics Athletics GARRETT, Robert USA Men High Jump Silver 1896 Athens Athletics Athletics CONNOLLY, James USA Men Long Jump Bronze 1896 Athens Athletics Athletics CLARK, Ellery USA Men Long Jump Gold 1896 Athens Athletics Athletics GARRETT, Robert USA Men Long Jump Silver 1896 Athens Athletics Athletics KELLNER, Gyula HUN Men Marathon Bronze 1896 Athens Athletics Athletics LOUIS, Spyridon GRE Men Marathon Gold 1896 Athens Athletics Athletics VASILAKOS, Kharilaos GRE Men Marathon Silver 1896 Athens Athletics Athletics DAMASKOS, Evangelos GRE Men Pole Vault Bronze 1896 Athens Athletics Athletics THEODOROPOULOS, Ioannis GRE Men Pole Vault Bronze 1896 Athens Athletics Athletics HOYT, William Welles USA Men Pole Vault Gold 1896 Athens Athletics Athletics TYLER, Albert USA Men Pole Vault Silver 1896 Athens Athletics Athletics PAPASIDERIS, Georgios GRE Men Shot Put Bronze 1896 Athens Athletics Athletics GARRETT, Robert USA Men Shot Put Gold 1896 Athens Athletics Athletics GOUSKOS, Miltiadis GRE Men Shot Put Silver 1896 Athens Athletics Athletics PERSAKIS, Ioannis GRE Men Triple Jump Bronze 1896 Athens Athletics Athletics CONNOLLY, James USA Men Triple Jump Gold 1896 Athens Athletics Athletics TUFFERI, Alexandre FRA Men Triple Jump Silver 1896 Athens Cycling Cycling Road BATTEL, Edward GBR Men Individual Road Race Bronze 1896 Athens Cycling Cycling Road KONSTANTINIDIS, Aristidis GRE Men Individual Road Race Gold 1896 Athens Cycling Cycling Road GOEDRICH, August GER Men Individual Road Race Silver 1896 Athens Cycling Cycling Track FLAMENG, Léon FRA Men 100KM Gold 1896 Athens Cycling Cycling Track KOLETTIS, Georgios GRE

In [0]:
# check number of records
olympics_data.count()

Out[2]: 31165

In [0]:
#overvrite data, performing partitioning by country, save as delta table
olympics_data.write \
             .partitionBy("Country") \
             .format("delta") \
             .mode("overwrite") \
             .save("dbfs:/FileStore/datasets/olympics_data")

In [0]:
spark.sql("CREATE TABLE olympics USING DELTA LOCATION 'dbfs:/FileStore/datasets/olympics_data'")

Out[4]: DataFrame[]

In [0]:
%sql

SELECT count(*) FROM olympics

count(1) 31165

In [0]:
%sql

SELECT min(Year), max(Year) FROM olympics

min(Year) max(Year) 1896 2012

In [0]:
%sql

SELECT count(*) as NumMedal, Gender, Medal FROM olympics WHERE Year = 2000 GROUP BY Gender, Medal

NumMedal Gender Medal 370 Men Gold 370 Men Silver 386 Men Bronze 299 Women Bronze 297 Women Silver 293 Women Gold

Z-ordering will co-locate data grouped by year (if applies). May not work on small dataset. In our case output shows that 0 files were relocated

In [0]:
%sql

OPTIMIZE olympics ZORDER BY (Year)

path metrics dbfs:/FileStore/datasets/olympics_data List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 148, List(minCubeSize(107374182400), List(0, 0), List(148, 914436), 0, List(0, 0), 0, null), 0, 148, 148, false)

Above we can see numFilesAdded: 0, numFilesRemoved: 0 both are zero so after zordering time taken by query will not reduce   
We can cross check it by running same query

In [0]:
%sql

SELECT count(*) as NumMedal, Gender, Medal FROM olympics WHERE Year = 2000 GROUP BY Gender, Medal

NumMedal Gender Medal 370 Men Gold 370 Men Silver 386 Men Bronze 299 Women Bronze 297 Women Silver 293 Women Gold

To check z -ordering performance on a larger scale we will upload a built-in dataset from Databricks resources. It is over 600 Gb -large

In [0]:
flight_data = spark.read.format("csv") \
                        .option("header", "true") \
                        .option("inferSchema", "true") \
                        .load("/databricks-datasets/asa/airlines/2005.csv")

flight_data.display()

Year Month DayofMonth DayOfWeek DepTime CRSDepTime ArrTime CRSArrTime UniqueCarrier FlightNum TailNum ActualElapsedTime CRSElapsedTime AirTime ArrDelay DepDelay Origin Dest Distance TaxiIn TaxiOut Cancelled CancellationCode Diverted CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay 2005 1 28 5 1603 1605 1741 1759 UA 541 N935UA 158 174 131 -18 -2 BOS ORD 867 4 23 0 null 0 0 0 0 0 0 2005 1 29 6 1559 1605 1736 1759 UA 541 N941UA 157 174 136 -23 -6 BOS ORD 867 6 15 0 null 0 0 0 0 0 0 2005 1 30 7 1603 1610 1741 1805 UA 541 N342UA 158 175 131 -24 -7 BOS ORD 867 9 18 0 null 0 0 0 0 0 0 2005 1 31 1 1556 1605 1726 1759 UA 541 N326UA 150 174 129 -33 -9 BOS ORD 867 11 10 0 null 0 0 0 0 0 0 2005 1 2 7 1934 1900 2235 2232 UA 542 N902UA 121 152 106 3 34 ORD BOS 867 5 10 0 null 0 0 0 0 0 0 2005 1 3 1 2042 1900 9 2232 UA 542 N904UA 147 152 97 97 102 ORD BOS 867 3 47 0 null 0 23 0 0 0 74 2005 1 4 2 2046 1900 2357 2232 UA 542 N942UA 131 152 100 85 106 ORD BOS 867 5 26 0 null 0 46 0 0 0 39 2005 1 5 3 NA 1900 NA 2232 UA 542 000000 NA 152 NA NA NA ORD BOS 867 0 0 1 B 0 0 0 0 0 0 2005 1 6 4 2110 1900 8 2223 UA 542 N920UA 118 143 101 105 130 ORD BOS 867 2 15 0 null 0 16 0 0 0 89 2005 1 7 5 1859 1900 2235 2223 UA 542 N340UA 156 143 96 12 -1 ORD BOS 867 4 56 0 null 0 0 0 0 0 0 2005 1 9 7 1859 1900 2205 2223 UA 542 N929UA 126 143 106 -18 -1 ORD BOS 867 5 15 0 null 0 0 0 0 0 0 2005 1 10 1 1917 1900 2240 2223 UA 542 N934UA 143 143 116 17 17 ORD BOS 867 3 24 0 null 0 17 0 0 0 0 2005 1 11 2 1935 1900 2259 2223 UA 542 N336UA 144 143 106 36 35 ORD BOS 867 6 32 0 null 0 0 0 1 0 35 2005 1 12 3 2038 1900 18 2223 UA 542 N920UA 160 143 111 115 98 ORD BOS 867 6 43 0 null 0 18 0 17 0 80 2005 1 13 4 2106 1900 9 2223 UA 542 N923UA 123 143 106 106 126 ORD BOS 867 6 11 0 null 0 13 0 0 0 93 2005 1 14 5 1919 1900 2228 2223 UA 542 N917UA 129 143 100 5 19 ORD BOS 867 9 20 0 null 0 0 0 0 0 0 2005 1 16 7 1911 1900 NA 2223 UA 542 N348UA NA 143 NA NA 11 ORD BOS 867 0 13 0 null 1 0 0 0 0 0 2005 1 17 1 1859 1900 2202 2223 UA 542 N902UA 123 143 109 -21 -1 ORD BOS 867 3 11 0 null 0 0 0 0 0 0 2005 1 18 2 1856 1900 2227 2223 UA 542 N906UA 151 143 117 4 -4 ORD BOS 867 3 31 0 null 0 0 0 0 0 0 2005 1 19 3 1939 1900 2348 2223 UA 542 N932UA 189 143 166 85 39 ORD BOS 867 6 17 0 null 0 10 0 46 0 29 2005 1 20 4 2128 1900 41 2223 UA 542 N910UA 133 143 111 138 148 ORD BOS 867 4 18 0 null 0 32 0 0 0 106 2005 1 21 5 1913 1900 2226 2223 UA 542 N934UA 133 143 110 3 13 ORD BOS 867 4 19 0 null 0 0 0 0 0 0 2005 1 23 7 NA 1900 NA 2223 UA 542 000000 NA 143 NA NA NA ORD BOS 867 0 0 1 B 0 0 0 0 0 0 2005 1 24 1 NA 1900 NA 2223 UA 542 000000 NA 143 NA NA NA ORD BOS 867 0 0 1 A 0 0 0 0 0 0 2005 1 25 2 1849 1900 2200 2223 UA 542 N929UA 131 143 108 -23 -11 ORD BOS 867 4 19 0 null 0 0 0 0 0 0 2005 1 26 3 NA 1900 NA 2223 UA 542 000000 NA 143 NA NA NA ORD BOS 867 0 0 1 A 0 0 0 0 0 0 2005 1 27 4 1859 1900 2215 2223 UA 542 N927UA 136 143 115 -8 -1 ORD BOS 867 8 13 0 null 0 0 0 0 0 0 2005 1 28 5 1855 1900 2218 2223 UA 542 N923UA 143 143 111 -5 -5 ORD BOS 867 7 25 0 null 0 0 0 0 0 0 2005 1 30 7 1858 1900 2212 2223 UA 542 N920UA 134 143 117 -11 -2 ORD BOS 867 7 10 0 null 0 0 0 0 0 0 2005 1 31 1 1858 1900 2215 2223 UA 542 N919UA 137 143 112 -8 -2 ORD BOS 867 6 19 0 null 0 0 0 0 0 0 2005 1 1 6 1704 1715 1919 1915 UA 543 N203UA 195 180 144 4 -11 BOS ORD 867 13 38 0 null 0 0 0 0 0 0 2005 1 2 7 1713 1715 1911 1915 UA 543 N392UA 178 180 140 -4 -2 BOS ORD 867 18 20 0 null 0 0 0 0 0 0 2005 1 3 1 1856 1715 2106 1915 UA 543 N916UA 190 180 158 111 101 BOS ORD 867 8 24 0 null 0 0 0 111 0 0 2005 1 4 2 1744 1715 1950 1915 UA 543 N927UA 186 180 167 35 29 BOS ORD 867 5 14 0 null 0 0 0 35 0 0 2005 1 5 3 NA 1715 NA 1915 UA 543 000000 NA 180 NA NA NA BOS ORD 867 0 0 1 B 0 0 0 0 0 0 2005 1 6 4 2046 1705 2221 1902 UA 543 N342UA 155 177 135 199 221 BOS ORD 867 6 14 0 null 0 0 0 199 0 0 2005 1 7 5 1704 1705 1926 1902 UA 543 N312UA 202 177 152 24 -1 BOS ORD 867 16 34 0 null 0 0 0 24 0 0 2005 1 9 7 1853 1705 2138 1902 UA 54

In [0]:
# dataset has over 7 mln. rows
flight_data.count()

Out[11]: 7140596

In [0]:
# now we're going to writa dataset into our DBFS storage in delta format, performing partitioning by "Origin" column
# we also will create a delta table from the saved dataset (must be saved in delta format)
flight_data.write \
           .partitionBy("Origin") \
           .format("delta") \
           .mode("overwrite") \
           .save("dbfs:/FileStore/datasets/flights_data")

spark.sql("CREATE TABLE flights_data USING DELTA LOCATION 'dbfs:/FileStore/datasets/flights_data'")

Out[12]: DataFrame[]

Now we can perform SQL queries on our delta table. Note that min and max values are among the metadata stored in delta format. This is why quering such a huge table took less than a second.

In [0]:
%sql

SELECT min(DayofMonth), max(DayofMonth) FROM flights_data

min(DayofMonth) max(DayofMonth) 1 31

In [0]:
%sql

SELECT mean(ArrDelay) AS Delay, Dest, Month FROM flights_data WHERE DayofMonth = 31 GROUP BY Month, Dest

Delay Dest Month -0.3564356435643564 ONT 5 22.75 MLU 10 5.363636363636363 JAX 10 7.575757575757576 OMA 7 2.765151515151515 CLE 10 11.5 EYW 1 12.8 LNK 3 12.0 ACY 1 -10.4 TWF 1 2.25 EKO 7 -1.4285714285714286 RDM 1 10.41025641025641 SYR 3 1.3297002724795641 IAD 5 11.321428571428571 BHM 10 -2.8333333333333335 AVP 10 2.0 COS 12 32.0 CSG 7 -2.878136200716846 MDW 8 1.948051948051948 RNO 8 1.8823529411764706 HPN 8 31.285714285714285 GNV 1 45.285714285714285 AEX 1 4.5 IYK 12 20.424242424242426 HSV 3 5.864864864864865 COS 5 6.639810426540285 TPA 5 0.33884297520661155 AUS 5 14.073170731707316 DAY 10 16.055555555555557 SHV 7 43.0 LWB 8 11.0 BRO 12 9.745098039215685 ALB 3 12.463414634146341 TYS 3 32.0 PHF 3 8.927710843373495 JAX 5 16.21875 OMA 10 2.48135593220339 DCA 10 74.15758468335788 DFW 10 6.555555555555555 ABE 1 7.125 CID 3 10.75 CLL 3 -6.111111111111111 ACT 3 10.333333333333334 JNU 8 12.25 BFL 10 1.3825 MSP 3 84.0 MCN 3 5.96969696969697 JAN 5 43.81481481481482 BTR 10 -6.96969696969697 MHT 10 17.75 LNK 10 11.666666666666666 YUM 10 -2.7777777777777777 IDA 8 -2.4 PSC 1 62.0 COD 12 -5.75 MOD 3 -12.4 JNU 1 11.114285714285714 GEG 12 48.333333333333336 FNT 3 0.27672955974842767 PDX 8 37.0 VCT 1 6.857142857142857 LIH 8 26.8 FCA 12 2.3333333333333335 MOD 12 7.60545905707196 DTW 3 8.875 MEM 10 4.699029126213592 MEM 12 23.75 ILM 12 6.0 LFT 12 1.0530503978779842 MSP 1 16.142857142857142 MLU 1 -6.333333333333333 CMI 12 5.473684210526316 FAT 5 -0.7391304347826086 BTV 10 -1.0 FAR 10 4.625 SUN 10 -2.0 IDA 7 6.254716981132075 BDL 3 11.5 ABE 5 0.3398268398268398 LAS 8 33.94444444444444 GPT 1 11.666666666666666 SMX 12 -8.0 VCT 5 13.0 MOT 5 2.16600790513834 MDW 3 2.8 DAY 5 31.650793650793652 TUL 10 11.133116883116884 MSP 12 6.605504587155964 HNL 7 0.7832699619771863 MDW 7 -1.6083916083916083 SLC 1 21.0 APF 1 -4.5 TYR 12 -0.07142857142857142 LAN 1 3.0 YUM 8 7.818181818181818 LIH 12 12.466666666666667 CAE 5 11.357142857142858 BZN 12 -14.5 MCN 12 3.094972067039106 IAD 7 15.428571428571429 ATW 8 3.923076923076923 ILM 8 9.55952380952381 BUR 10 0.36538461538461536 ALB 1 3.195876288659794 ABQ 1 10.333333333333334 SPS 3 -1.3333333333333333 TXK 7 -16.0 DRO 5 -4.625 SUN 5 -1.0 STX 5 6.310344827586207 DSM 3 0.31989247311827956 LGA 5 15.0 AGS 12 11.642857142857142 MKE 7 4.468354430379747 BUR 3 21.0 ABI 1 -4.0 DRO 8 -1.7142857142857142 EUG 10 -18.0 PSE 8 18.678571428571427 BTR 5 7.2592592592592595 DSM 5 0.09 BWI 10 5.3695014662756595 MSP 10 11.32258064516129 ORF 7 10.642857142857142 LAN 3 -4.0 LCH 7 -8.842105263157896 LIH 10 0.45454545454545453 FCA 8 0.0 HLN 1 4.0 STX 10 -5.333333333333333 STT 5 -1.5174603174603174 LAX 10 3.5491400491400493 ORD 12 9.085106382978724 MSY 12 71.66666666666667 APF 7 7.773006134969325 HOU 1 2.287878787878788 ORF 1 -6.4 FCA 1 18.651162790697676 JAX 3 1.2361111111111112 MHT 3 25.333333333333332 BQK 3 -5.75 ABE 10 -5.0 CRW 12 7.0 VLD 8 22.333333333333332 FAY 8 12.793103448275861 JAN 1 20.5 DHN 1 4.7272727272727275 BTV 3 5.857142857142857 GTF 10 5.75 BTM 8 0.4117647058823529 EUG 5 3.0 BTM 1 -11.5 FLO 10 1.2976190476190477 RDU 10 18.25 BQK 8 17.1875 PSP 10 14.384615384615385 LBB 3 8.0 BGM 1 0.6470588235294118 HRL 3 -12.25 HLN 12 -4.0 RDD 7 1.76 CRP 3 3.6491228070175437 LIT 5 16.0 FLO 12 5.5625 PHF 8 16.267857142857142 SJU 10 -4.666666666666667 GGG 8 1.1428571428571428 STT 12 0.25 GNV 12 2.207667731629393 SEA 8 2.9166666666666665 LBB 1 3.6785714285714284 ROC 5 19.666666666666668 APF 5 4.478260869565218 TYS 12 13.512820512820513 GRR 12 8.727272727272727 CRW 7 5.636363636363637 ABE 7 -3.6 MLU 8 7.142857142857143 LAW 3 -6.5 SPS 7 0.2 OXR 10 23.666666666666668 MOT 7 13.75 CSG 3 15.685714285714285 SEA 5 -1.455128205128205 PIT 5 -3.25 ABY 10 -1.4166666666666667 AZO 12 -5.0 ALB 10 0.6706586826347305 BNA 1 5.25 BTV 7 5.5625 MFR 7 13.852941176470589 PNS 5 -15.0 LWB 5 1.4 ISP 12 -0.1836734693877551 IAD 8 4.323529411764706 CMH 10 -0.2765957446808511 GSO 10 12.454545454545455 TUS 10 16.0 PIA 1 -3.125 HRL 7 16.0 ERI 12 26.0 CIC 10 7.292929292929293 ABQ 3 

Such an coplex query above took around 29 seconds on a large dataset. We'll try to optimize performance by applying Z-ordering by "DayofMonth". It should co-locate same date data. It is a heavy operation that took 3.51 min on my cluster

In [0]:
%sql

OPTIMIZE flights_data ZORDER BY (DayofMonth)

path metrics dbfs:/FileStore/datasets/flights_data List(282, 1378, List(10359, 6929189, 381674.3758865248, 282, 107632174), List(7635, 1540077, 90468.89259796806, 1378, 124666134), 286, List(minCubeSize(107374182400), List(0, 0), List(1382, 124694411), 0, List(1378, 124666134), 282, null), 1, 1382, 4, false)

Let's re-run the previous complex SQL query and observe changes in its performance. Now it takes 8.2 seconds to run what is a large improvement

In [0]:
%sql

SELECT mean(ArrDelay) AS Delay, Dest, Month FROM flights_data WHERE DayofMonth = 31 GROUP BY Month, Dest

Delay Dest Month -0.3564356435643564 ONT 5 22.75 MLU 10 5.363636363636363 JAX 10 7.575757575757576 OMA 7 2.765151515151515 CLE 10 11.5 EYW 1 12.8 LNK 3 12.0 ACY 1 -10.4 TWF 1 2.25 EKO 7 -1.4285714285714286 RDM 1 10.41025641025641 SYR 3 1.3297002724795641 IAD 5 11.321428571428571 BHM 10 -2.8333333333333335 AVP 10 2.0 COS 12 32.0 CSG 7 -2.878136200716846 MDW 8 1.948051948051948 RNO 8 1.8823529411764706 HPN 8 31.285714285714285 GNV 1 45.285714285714285 AEX 1 4.5 IYK 12 20.424242424242426 HSV 3 5.864864864864865 COS 5 6.639810426540285 TPA 5 0.33884297520661155 AUS 5 14.073170731707316 DAY 10 16.055555555555557 SHV 7 43.0 LWB 8 11.0 BRO 12 9.745098039215685 ALB 3 12.463414634146341 TYS 3 32.0 PHF 3 8.927710843373495 JAX 5 16.21875 OMA 10 2.48135593220339 DCA 10 74.15758468335788 DFW 10 6.555555555555555 ABE 1 7.125 CID 3 10.75 CLL 3 -6.111111111111111 ACT 3 12.25 BFL 10 1.3825 MSP 3 84.0 MCN 3 5.96969696969697 JAN 5 43.81481481481482 BTR 10 -6.96969696969697 MHT 10 17.75 LNK 10 11.666666666666666 YUM 10 -2.4 PSC 1 -2.7777777777777777 IDA 8 62.0 COD 12 -5.75 MOD 3 11.114285714285714 GEG 12 48.333333333333336 FNT 3 0.27672955974842767 PDX 8 37.0 VCT 1 6.857142857142857 LIH 8 26.8 FCA 12 2.3333333333333335 MOD 12 7.60545905707196 DTW 3 8.875 MEM 10 4.699029126213592 MEM 12 23.75 ILM 12 6.0 LFT 12 1.0530503978779842 MSP 1 16.142857142857142 MLU 1 -6.333333333333333 CMI 12 -0.7391304347826086 BTV 10 -1.0 FAR 10 5.473684210526316 FAT 5 4.625 SUN 10 -2.0 IDA 7 6.254716981132075 BDL 3 11.5 ABE 5 0.3398268398268398 LAS 8 33.94444444444444 GPT 1 -8.0 VCT 5 11.666666666666666 SMX 12 13.0 MOT 5 2.16600790513834 MDW 3 2.8 DAY 5 31.650793650793652 TUL 10 11.133116883116884 MSP 12 6.605504587155964 HNL 7 0.7832699619771863 MDW 7 -1.6083916083916083 SLC 1 21.0 APF 1 -0.07142857142857142 LAN 1 -4.5 TYR 12 3.0 YUM 8 7.818181818181818 LIH 12 12.466666666666667 CAE 5 11.357142857142858 BZN 12 -14.5 MCN 12 3.094972067039106 IAD 7 15.428571428571429 ATW 8 3.923076923076923 ILM 8 9.55952380952381 BUR 10 0.36538461538461536 ALB 1 3.195876288659794 ABQ 1 10.333333333333334 SPS 3 -1.3333333333333333 TXK 7 -16.0 DRO 5 -4.625 SUN 5 6.310344827586207 DSM 3 0.31989247311827956 LGA 5 15.0 AGS 12 11.642857142857142 MKE 7 4.468354430379747 BUR 3 21.0 ABI 1 -4.0 DRO 8 -1.7142857142857142 EUG 10 -18.0 PSE 8 18.678571428571427 BTR 5 7.2592592592592595 DSM 5 0.09 BWI 10 5.3695014662756595 MSP 10 11.32258064516129 ORF 7 10.642857142857142 LAN 3 -4.0 LCH 7 -8.842105263157896 LIH 10 0.45454545454545453 FCA 8 0.0 HLN 1 -5.333333333333333 STT 5 -1.5174603174603174 LAX 10 3.5491400491400493 ORD 12 9.085106382978724 MSY 12 71.66666666666667 APF 7 7.773006134969325 HOU 1 2.287878787878788 ORF 1 -6.4 FCA 1 18.651162790697676 JAX 3 1.2361111111111112 MHT 3 25.333333333333332 BQK 3 -5.75 ABE 10 -5.0 CRW 12 7.0 VLD 8 22.333333333333332 FAY 8 12.793103448275861 JAN 1 20.5 DHN 1 4.7272727272727275 BTV 3 5.857142857142857 GTF 10 0.4117647058823529 EUG 5 5.75 BTM 8 3.0 BTM 1 -11.5 FLO 10 1.2976190476190477 RDU 10 18.25 BQK 8 17.1875 PSP 10 14.384615384615385 LBB 3 0.6470588235294118 HRL 3 8.0 BGM 1 -12.25 HLN 12 -4.0 RDD 7 1.76 CRP 3 3.6491228070175437 LIT 5 16.0 FLO 12 5.5625 PHF 8 16.267857142857142 SJU 10 -4.666666666666667 GGG 8 1.1428571428571428 STT 12 0.25 GNV 12 2.207667731629393 SEA 8 2.9166666666666665 LBB 1 3.6785714285714284 ROC 5 19.666666666666668 APF 5 4.478260869565218 TYS 12 13.512820512820513 GRR 12 8.727272727272727 CRW 7 5.636363636363637 ABE 7 -3.6 MLU 8 7.142857142857143 LAW 3 -6.5 SPS 7 0.2 OXR 10 23.666666666666668 MOT 7 13.75 CSG 3 15.685714285714285 SEA 5 -1.455128205128205 PIT 5 -3.25 ABY 10 -1.4166666666666667 AZO 12 -5.0 ALB 10 0.6706586826347305 BNA 1 5.25 BTV 7 5.5625 MFR 7 13.852941176470589 PNS 5 -15.0 LWB 5 1.4 ISP 12 -0.1836734693877551 IAD 8 4.323529411764706 CMH 10 -0.2765957446808511 GSO 10 12.454545454545455 TUS 10 16.0 PIA 1 -3.125 HRL 7 16.0 ERI 12 26.0 CIC 10 7.292929292929293 ABQ 3 4.714285714285714 MSY 5 3.121495327102804 ABQ 7 11.78571428